### Ahora con la formula de Borovicka

In [17]:
from scipy import optimize, stats
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from tqdm import tqdm

In [51]:
X0, Y0, a0 = float(724), float(472), float(-3*np.pi/4) #x=724 parece una mejor opcion

In [43]:
def construct_radio(C, A, F):
    def r(x, y):
        return C * ( np.sqrt( (x-X0)**2 + (y-Y0)**2 ) + A*(y-X0)*np.cos(F-a0) - A*(x-X0)*np.sin(F-a0) )
    return r

def construct_u(C, A, F, V, S, D, P, Q):
    def u(x, y):
        r = construct_radio(C, A, F)
        return V*r(x, y) + S*(np.e**(D*r(x,y)) - 1) + P*(np.e**(Q*r(x,y)**2) - 1) 
    return u

def construct_b(E):
    def b(x, y):
        return a0 - E + np.arctan2((y - Y0),(x - X0))
    return b

def construct_altura(C, A, F, V, S, D, P, Q, E, ep):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        return np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) )
    return z

def construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        return 90 - np.rad2deg( np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) ) )
    return z

def construct_azimuth(C, A, F, V, S, D, P, Q, E, ep):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep)
        return np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E
    return az

def construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep)
        return np.rad2deg( np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E )
    return az

In [44]:
def plot_plano(plano):
    x = np.linspace(0, 1200, 100)
    y = np.linspace(0, 900, 100)
    X, Y = np.meshgrid(x, y)
    Z = plano(X, Y)
    fig,ax=plt.subplots(1,1)
    cp = ax.contourf(X, Y, Z, 10)
    fig.colorbar(cp) # Add a colorbar to a plot
    ax.set_title('Toda una linea que minimiza y=mx+n')
    plt.gca().invert_yaxis()
    ax.set_xlabel('x')
    ax.set_ylabel('y')
    plt.show()

def plot_altura(vector):
    plano = construct_altura_deg(*vector)
    plot_plano(plano)
    
def plot_azimuth(vector):
    plano = construct_azimuth_deg(*vector)
    plot_plano(plano)

In [68]:
def drop_outlayers_by_center(pixtab_df, x0, y0, Z_VALUE = 0.5):
    
    X_MIN = 250
    X_MAX = 1250
    Y_MIN = 0
    Y_MAX = 950
    MAX_RADIO = 500
    RADIO_STEPS = 2000
    query_str = "{}<=x<={} and {}<=y<={}".format(X_MIN, X_MAX,
                                                            Y_MIN, Y_MAX)
    data = pixtab_df.dropna(thresh = 7).query(query_str)
    
    r_list = []
    for indx in data.index:
        x = data.at[indx,"x"]
        y = data.at[indx,"y"]
        r = np.sqrt((x - x0)**2 + (y - y0)**2)
        r_list.append(r)
    data["radio"] = r_list

    rstep = MAX_RADIO/(RADIO_STEPS-1)
    r_range = np.linspace(0, MAX_RADIO, RADIO_STEPS)
    pbar = tqdm(total=RADIO_STEPS, desc="Droping Outlayers")
    new_df = []
    for r in r_range:
        query = "radio > {} and radio <= {}".format(r, r+rstep)
        df_circle = data.query(query).dropna()
        if len(df_circle)==1:
            new_df.append(df_circle)
        elif len(df_circle)>1:
            z = stats.zscore(df_circle.alt.values)
            indx = np.where(np.abs(z) < Z_VALUE)
            new_df.append(df_circle.loc[df_circle.index.values[indx]])
        pbar.update()
    pbar.close()
    new_df = pd.concat(new_df, ignore_index=True)
    return new_df

# out = drop_outlayers_by_center(data, X0, Y0)
# out
# out["xcentroid"] = out["x"]
# out["ycentroid"] = out["y"]
# out.to_csv("drop_outlayer.dat", sep=' ', index=False)
# plt.gca().invert_yaxis()
# plt.scatter(out.x.values, out.y.values, c=out.alt.values, s=0.01)

In [180]:
def drop_outlayers_by_borovicka(pixtab_df, plano, diff = 1):
    
    X_MIN = 250
    X_MAX = 1250
    Y_MIN = 0
    Y_MAX = 950
    MAX_RADIO = 500
    RADIO_STEPS = 2000
    query_str = "{}<=x<={} and {}<=y<={}".format(X_MIN, X_MAX,
                                                            Y_MIN, Y_MAX)
    data = pixtab_df.dropna(thresh = 7).query(query_str)
    
    pbar = tqdm(total=len(data.x.values), desc="Droping Outlayers")
    new_df_indx = []
    for indx in data.index:
        x = data.at[indx,"x"]
        y = data.at[indx,"y"]
        alt = data.at[indx,"alt"]
        if np.abs(plano(x,y)-alt) < diff:
            new_df_indx.append(indx)
        pbar.update()
    return data.loc[new_df_indx]

# out = drop_outlayers_by_borovicka(data, X0, Y0)
# out
# out["xcentroid"] = out["x"]
# out["ycentroid"] = out["y"]
# out.to_csv("drop_outlayer.dat", sep=' ', index=False)
# plt.gca().invert_yaxis()
# plt.scatter(out.x.values, out.y.values, c=out.alt.values, s=0.01)

In [90]:
def construct_alt_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep):
        alt_teorico = construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep)
        return (z - alt_teorico(x, y))**2
    return xi

def construct_acumulate_alt_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep)
        pbar.update()
        return suma_xi
    return acumulate_xi

def construct_az_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep):
        az_teorico = construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep)
        return (z - az_teorico(x, y))**2
    return xi

def construct_acumulate_az_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_az_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep)
        pbar.update()
        return suma_xi
    return acumulate_xi

In [23]:
def amoeba(params, mega_alt_xi, mega_az_xi):
    new_alt_params = optimize.fmin(mega_alt_xi, params, maxfun=2200)
#     new_az_params = optimize.fmin(mega_az_xi, params, maxfun=110)
    return [new_alt_params]

In [53]:
%matplotlib qt

data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
data = drop_outlayers_by_center(data, X0, Y0)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = data.az.values
# plt.gca().invert_yaxis()
# plt.scatter(x_exp, y_exp, c=alt_catalogo, s=0.01)



Droping Outlayers:   0%|                                                                      | 0/2000 [00:00<?, ?it/s]

Droping Outlayers:   1%|▋                                                           | 24/2000 [00:00<00:08, 238.21it/s]

Droping Outlayers:   2%|█▍                                                          | 49/2000 [00:00<00:08, 239.04it/s]

Droping Outlayers:   4%|██▏                                                         | 73/2000 [00:00<00:08, 238.81it/s]

Droping Outlayers:   5%|██▉                                                         | 96/2000 [00:00<00:08, 235.59it/s]

Droping Outlayers:   6%|███▌                                                       | 119/2000 [00:00<00:08, 231.95it/s]

Droping Outlayers:   7%|████▏                                                      | 142/2000 [00:00<00:08, 230.16it/s]

Droping Outlayers:   8%|████▊                                                      | 165/2000 [00:00<00:08, 228.91it/s]

Droping Outlayers:   9%|█████▌

Droping Outlayers:  80%|██████████████████████████████████████████████▎           | 1596/2000 [00:06<00:01, 230.19it/s]

Droping Outlayers:  81%|██████████████████████████████████████████████▉           | 1620/2000 [00:07<00:01, 231.22it/s]

Droping Outlayers:  82%|███████████████████████████████████████████████▋          | 1644/2000 [00:07<00:01, 230.60it/s]

Droping Outlayers:  83%|████████████████████████████████████████████████▎         | 1668/2000 [00:07<00:01, 229.53it/s]

Droping Outlayers:  85%|█████████████████████████████████████████████████         | 1691/2000 [00:07<00:01, 229.15it/s]

Droping Outlayers:  86%|█████████████████████████████████████████████████▋        | 1714/2000 [00:07<00:01, 228.22it/s]

Droping Outlayers:  87%|██████████████████████████████████████████████████▎       | 1737/2000 [00:07<00:01, 227.59it/s]

Droping Outlayers:  88%|███████████████████████████████████████████████████       | 1761/2000 [00:07<00:01, 230.02it/s]

Droping Outlayers:  89%|████████

In [25]:
C, A, F = 0.07, 0.01, 1
V, S, D, P, Q = 0.03, 0.007, 0.09, 2.2*10**-6, 0.006
E, ep = 0, 0

mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo)
results_list = []

In [26]:
for i in range(4):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba([C,A,F,V,S,D,P,Q,E,ep], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]


Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:03<2:19:04,  3.79s/it]

KeyboardInterrupt: 

### Resultados con la configuracion actual

Con centro $x=757$, $y=472$ y $a0=0$ y usando todos los datos

In [58]:
X0, Y0, a0 = float(757), float(472), float(0)

In [59]:
result1 = np.array([ 4.05411155*10**-2, -5.13000215*10**-2,  1.18306086,  8.18813843*10**-2,
       -3.63276373*10**-3, -1.22830557,  1.09298238*10**-5,  1.29796815*10**-2,
        2.09851909*10**-3,  5.53361549*10**-2])
result2 = np.array([ 2.90396335*10**-2, -1.36275018*10**-2, -2.42156457*10**-1,  1.14623453*10**-1,
       -6.22511285*10**-3, -4.72148386,  4.53040216*10**-5,  1.57578545*10**-2,
       -3.35189511*10**-2,  1.03652889*10**-1])
result3 = np.array([ 2.87039016*10**-2, -5.47881381*10**-3, -2.49778009*10**-1,  1.14866070*10**-1,
       -2.19097809*10**-2, -4.58387917*10**-1,  2.62567843*10**-4,  2.39744298*10**-2,
       -1.06146519*10**-1,  1.02486171*10**-1])
result4 = np.array([ 0.02863326, -0.00550686, -0.30656714,  0.11274438, -0.03916933,
       -0.29909259,  0.00547779,  0.01104806, -0.10624677,  0.1027069 ])
result5 = np.array([ 0.02896625, -0.00554929, -0.3355378 ,  0.11107163, -0.04046421,
       -0.29994853,  0.00962758,  0.00862338, -0.10597777,  0.10286461])

In [60]:
(mega_alt_xi(result1)/len(x_exp), mega_alt_xi(result2)/len(x_exp),
 mega_alt_xi(result3)/len(x_exp), mega_alt_xi(result4)/len(x_exp),
 mega_alt_xi(result5)/len(x_exp))


Aproximando altura y azimuth:   2%|█▏                                              | 53/2200 [41:53<5:31:56,  9.28s/it]

(3.417301236112704,
 2.776068690339051,
 2.7564699510172916,
 2.754597924132028,
 2.754326082216683)

No está bien quedarse con esto porque x0 está mal ahi, además a0 no puede ser 0

Con centro $x=724$, $y=472$ y $a0=\frac{-3\pi}{4}$

In [63]:
X0, Y0, a0 = float(724), float(472), float(-3*np.pi/4)

In [61]:
results_list_z05 = [np.array([ 4.88504077e-02,  2.02995372e-02,  3.51610379e-01,  6.82171007e-02,
         3.10608468e-03, -5.75141386e-05,  4.26865327e-06, -4.15889519e-03,
         2.21040767e-03,  1.47892726e-03]),
 np.array([ 4.88504077e-02,  2.02995372e-02,  3.51610379e-01,  6.82171007e-02,
         3.10608468e-03, -5.75141386e-05,  4.26865327e-06, -4.15889519e-03,
         2.21040767e-03,  1.47892726e-03]),
 np.array([ 4.88504077e-02,  2.02995372e-02,  3.51610379e-01,  6.82171007e-02,
         3.10608468e-03, -5.75141386e-05,  4.26865327e-06, -4.15889519e-03,
         2.21040767e-03,  1.47892726e-03]),
 np.array([ 4.88504077e-02,  2.02995372e-02,  3.51610379e-01,  6.82171007e-02,
         3.10608468e-03, -5.75141386e-05,  4.26865327e-06, -4.15889519e-03,
         2.21040767e-03,  1.47892726e-03])]
results_list_z1 = [np.array([ 6.68386793e-02,  2.11643138e-02,  3.95994947e-01,  4.97793056e-02,
        -1.98285373e-04,  3.95323036e-02,  1.77167244e-06,  8.38067924e-03,
         4.35828992e-04,  2.52528618e-03]),
 np.array([ 6.68386793e-02,  2.11643138e-02,  3.95994947e-01,  4.97793056e-02,
        -1.98285373e-04,  3.95323036e-02,  1.77167244e-06,  8.38067924e-03,
         4.35828992e-04,  2.52528618e-03]),
 np.array([ 6.68386793e-02,  2.11643138e-02,  3.95994947e-01,  4.97793056e-02,
        -1.98285373e-04,  3.95323036e-02,  1.77167244e-06,  8.38067924e-03,
         4.35828992e-04,  2.52528618e-03]),
 np.array([ 6.68386793e-02,  2.11643138e-02,  3.95994947e-01,  4.97793056e-02,
        -1.98285373e-04,  3.95323036e-02,  1.77167244e-06,  8.38067924e-03,
         4.35828992e-04,  2.52528618e-03])]

In [64]:
(mega_alt_xi(results_list_z05[-1])/len(x_exp), mega_alt_xi(results_list_z1[-1])/len(x_exp),
 mega_alt_xi(result3)/len(x_exp))


Aproximando altura y azimuth:   3%|█▎                                              | 59/2200 [44:28<8:26:06, 14.18s/it]

(2.810622513345362, 2.813157449737228, 31.782596665091102)

### Ahora intentaremos párametros de la manera Borovicka

#### Reduction types:

There are many types as mentioned in the section 2.2.3. of the paper.
However, IRED may be zero when entering REDSKY. Then the standard
reduction type 314 is used. The most usual types are

314 - V,S,D,P,Q kept at their standard values, other constants computed

334 - P,Q kept, C=1, other computed

354 - C=1, other computed (requires stars close to horizon)

311 - as 314 but A=0, F=0 (similarly 331, 351)

310 - as 311 but also epsilon=0, E=0 (similarly 330, 350)

319 - as 314 but epsilon,E,A,F kept at their initial values (similarly
      339, 359)

#### 314 - V,S,D,P,Q kept at their standard values, other constants computed

In [66]:
"""
Redefinimos el Xi para que no dependa de V,S,D,P,Q
Resultados con x0=724, y=472, a0=-3*np.pi/4
y habiendo reducido datos con z=05
"""
V, S, D, P, Q = results_list_z05[-1][3:8]
def construct_acumulate_alt_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep)
        pbar.update()
        return suma_xi
    return acumulate_xi

In [69]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
data = drop_outlayers_by_center(data, X0, Y0)
x = (data.x.values)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = data.az.values
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo)
results_list = []



Droping Outlayers:   0%|                                                                      | 0/2000 [00:00<?, ?it/s]

Droping Outlayers:   1%|▋                                                           | 22/2000 [00:00<00:09, 217.85it/s]

Droping Outlayers:   2%|█▎                                                          | 45/2000 [00:00<00:08, 218.93it/s]

Droping Outlayers:   3%|██                                                          | 67/2000 [00:00<00:08, 217.47it/s]

Droping Outlayers:   4%|██▋                                                         | 89/2000 [00:00<00:08, 217.76it/s]

Droping Outlayers:   6%|███▎                                                       | 111/2000 [00:00<00:08, 218.03it/s]

Droping Outlayers:   7%|███▉                                                       | 134/2000 [00:00<00:08, 220.03it/s]

Droping Outlayers:   8%|████▋                                                      | 158/2000 [00:00<00:08, 223.64it/s]

Droping Outlayers:   9%|█████▎

Droping Outlayers:  79%|█████████████████████████████████████████████▉            | 1585/2000 [00:06<00:01, 231.61it/s]

Droping Outlayers:  80%|██████████████████████████████████████████████▋           | 1609/2000 [00:07<00:01, 232.87it/s]

Droping Outlayers:  82%|███████████████████████████████████████████████▎          | 1633/2000 [00:07<00:01, 233.10it/s]

Droping Outlayers:  83%|████████████████████████████████████████████████          | 1657/2000 [00:07<00:01, 233.96it/s]

Droping Outlayers:  84%|████████████████████████████████████████████████▋         | 1681/2000 [00:07<00:01, 232.83it/s]

Droping Outlayers:  85%|█████████████████████████████████████████████████▍        | 1705/2000 [00:07<00:01, 230.79it/s]

Droping Outlayers:  86%|██████████████████████████████████████████████████▏       | 1729/2000 [00:07<00:01, 231.26it/s]

Droping Outlayers:  88%|██████████████████████████████████████████████████▊       | 1753/2000 [00:07<00:01, 231.96it/s]

Droping Outlayers:  89%|████████

In [81]:
results_list += amoeba([C, A, F, E, ep], mega_alt_xi, mega_az_xi)
for i in range(3):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba(results_list[-1], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]



Aproximando altura y azimuth:   0%|                                                           | 0/2200 [00:00<?, ?it/s]

Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:02<1:14:03,  2.02s/it]

Aproximando altura y azimuth:   0%|                                                 | 2/2200 [00:04<1:14:02,  2.02s/it]

Aproximando altura y azimuth:   0%|                                                 | 3/2200 [00:06<1:13:48,  2.02s/it]

Aproximando altura y azimuth:   0%|                                                 | 4/2200 [00:08<1:14:09,  2.03s/it]

Aproximando altura y azimuth:   0%|                                                 | 5/2200 [00:10<1:14:08,  2.03s/it]

Aproximando altura y azimuth:   0%|▏                                                | 6/2200 [00:12<1:14:27,  2.04s/it]

Aproximando altura y azimuth:   0%|▏                                                | 7/2200 [00:14<1:14:17,  2.03s/it]

Aproximando altura y azimuth: 

Aproximando altura y azimuth:   3%|█▍                                              | 67/2200 [02:14<1:11:55,  2.02s/it]

Aproximando altura y azimuth:   3%|█▍                                              | 68/2200 [02:16<1:12:02,  2.03s/it]

Aproximando altura y azimuth:   3%|█▌                                              | 69/2200 [02:18<1:11:33,  2.01s/it]

Aproximando altura y azimuth:   3%|█▌                                              | 70/2200 [02:20<1:11:24,  2.01s/it]

Aproximando altura y azimuth:   3%|█▌                                              | 71/2200 [02:22<1:11:34,  2.02s/it]

Aproximando altura y azimuth:   3%|█▌                                              | 72/2200 [02:24<1:11:25,  2.01s/it]

Aproximando altura y azimuth:   3%|█▌                                              | 73/2200 [02:26<1:11:09,  2.01s/it]

Aproximando altura y azimuth:   3%|█▌                                              | 74/2200 [02:28<1:11:01,  2.00s/it]

Aproximando altura y azimuth:   

Aproximando altura y azimuth:   6%|██▊                                            | 134/2200 [04:29<1:09:20,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 135/2200 [04:31<1:09:11,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 136/2200 [04:33<1:09:06,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 137/2200 [04:35<1:08:55,  2.00s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 138/2200 [04:37<1:09:05,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 139/2200 [04:39<1:08:53,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 140/2200 [04:41<1:08:52,  2.01s/it]

Aproximando altura y azimuth:   6%|███                                            | 141/2200 [04:43<1:08:51,  2.01s/it]

Aproximando altura y azimuth:   

Aproximando altura y azimuth:   9%|████▎                                          | 201/2200 [06:44<1:07:02,  2.01s/it]

Aproximando altura y azimuth:   9%|████▎                                          | 202/2200 [06:46<1:07:11,  2.02s/it]

Aproximando altura y azimuth:   9%|████▎                                          | 203/2200 [06:48<1:07:01,  2.01s/it]

Aproximando altura y azimuth:   9%|████▎                                          | 204/2200 [06:50<1:06:56,  2.01s/it]

Aproximando altura y azimuth:   9%|████▍                                          | 205/2200 [06:52<1:06:49,  2.01s/it]

Aproximando altura y azimuth:   9%|████▍                                          | 206/2200 [06:54<1:06:46,  2.01s/it]

Aproximando altura y azimuth:   9%|████▍                                          | 207/2200 [06:56<1:06:36,  2.01s/it]

Aproximando altura y azimuth:   9%|████▍                                          | 208/2200 [06:58<1:06:29,  2.00s/it]

Aproximando altura y azimuth:  1

Aproximando altura y azimuth:  12%|█████▋                                         | 268/2200 [08:58<1:04:19,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▋                                         | 269/2200 [09:00<1:04:34,  2.01s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 270/2200 [09:02<1:04:27,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 271/2200 [09:04<1:04:18,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 272/2200 [09:06<1:04:06,  1.99s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 273/2200 [09:08<1:04:09,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 274/2200 [09:10<1:04:08,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▉                                         | 275/2200 [09:12<1:04:08,  2.00s/it]

Aproximando altura y azimuth:  1

...

Aproximando altura y azimuth:  18%|████████▌                                      | 401/2200 [13:27<1:00:35,  2.02s/it]

Aproximando altura y azimuth:  18%|████████▌                                      | 402/2200 [13:29<1:00:17,  2.01s/it]

Aproximando altura y azimuth:  18%|████████▌                                      | 403/2200 [13:32<1:00:33,  2.02s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 404/2200 [13:33<1:00:08,  2.01s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 405/2200 [13:35<1:00:01,  2.01s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 406/2200 [13:38<1:00:09,  2.01s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 407/2200 [13:40<1:00:14,  2.02s/it]

Aproximando altura y azimuth:  19%|████████▋                                      | 408/2200 [13:42<1:00:07,  2.01s/it]

Aproximando altura y azimuth:  1

Aproximando altura y azimuth:  21%|██████████▍                                      | 468/2200 [15:43<58:03,  2.01s/it]

Aproximando altura y azimuth:  21%|██████████▍                                      | 469/2200 [15:45<58:11,  2.02s/it]

Aproximando altura y azimuth:  21%|██████████▍                                      | 470/2200 [15:47<58:04,  2.01s/it]

Aproximando altura y azimuth:  21%|██████████▍                                      | 471/2200 [15:49<58:00,  2.01s/it]

Aproximando altura y azimuth:  21%|██████████▌                                      | 472/2200 [15:51<58:04,  2.02s/it]

Aproximando altura y azimuth:  22%|██████████▌                                      | 473/2200 [15:53<58:09,  2.02s/it]

Aproximando altura y azimuth:  22%|██████████▌                                      | 474/2200 [15:55<58:00,  2.02s/it]

Aproximando altura y azimuth:  22%|██████████▌                                      | 475/2200 [15:57<57:49,  2.01s/it]

Aproximando altura y azimuth:  2

Optimization terminated successfully.
         Current function value: 5870.324582
         Iterations: 315
         Function evaluations: 524


Aproximando altura y azimuth:  24%|███████████▋                                     | 524/2200 [17:35<56:16,  2.01s/it]


array([0.04884979, 0.02030483, 0.35248629, 0.00538374, 0.00149506])

In [92]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = data.az.values
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)

In [88]:
result_314 = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664, 0.0682171007,
                         0.00310608468, -5.75141386e-05, 4.26865327e-06, -0.00415889519,
                           0.005383738310580881, 0.0014950622892165601])

In [94]:
mega_alt_xi(result_314)/len(x_exp)

2.206150388035022

#### Probamos con mover x0, y0, a0

In [95]:
"""
Agregamos como parametros variables x0, y0, a0
"""
def construct_radio(C, A, F, X0, Y0, a0):
    def r(x, y):
        return C * ( np.sqrt( (x-X0)**2 + (y-Y0)**2 ) + A*(y-X0)*np.cos(F-a0) - A*(x-X0)*np.sin(F-a0) )
    return r

def construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0):
    def u(x, y):
        r = construct_radio(C, A, F, X0, Y0, a0)
        return V*r(x, y) + S*(np.e**(D*r(x,y)) - 1) + P*(np.e**(Q*r(x,y)**2) - 1) 
    return u

def construct_b(E, X0, Y0, a0):
    def b(x, y):
        return a0 - E + np.arctan2((y - Y0),(x - X0))
    return b

def construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        return np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) )
    return z

def construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        return 90 - np.rad2deg( np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) ) )
    return z

def construct_azimuth(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E
    return az

def construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return np.rad2deg( np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E )
    return az

In [96]:
def construct_alt_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
        alt_teorico = construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return (z - alt_teorico(x, y))**2
    return xi

def construct_acumulate_alt_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0 = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        pbar.update()
        return suma_xi
    return acumulate_xi

def construct_az_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
        az_teorico = construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return (z - az_teorico(x, y))**2
    return xi

def construct_acumulate_az_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0 = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_az_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        pbar.update()
        return suma_xi
    return acumulate_xi

In [102]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = data.az.values
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
results_list = []

init_params = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664, 0.0682171007,
                         0.00310608468, -5.75141386e-05, 4.26865327e-06, -0.00415889519,
                           0.005383738310580881, 0.0014950622892165601, float(724), float(472), float(-3*np.pi/4)])

In [104]:
pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
results_list += amoeba(init_params, mega_alt_xi, mega_az_xi)
pbar.close()
for i in range(3):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba(results_list[-1], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]





Aproximando altura y azimuth:   0%|                                                           | 0/2200 [00:00<?, ?it/s]



Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:05<3:35:44,  5.89s/it]



Aproximando altura y azimuth:   0%|                                                 | 2/2200 [00:11<3:34:57,  5.87s/it]



Aproximando altura y azimuth:   0%|                                                 | 3/2200 [00:17<3:34:12,  5.85s/it]



Aproximando altura y azimuth:   0%|                                                 | 4/2200 [00:23<3:33:21,  5.83s/it]



Aproximando altura y azimuth:   0%|                                                 | 5/2200 [00:29<3:37:05,  5.93s/it]



Aproximando altura y azimuth:   0%|▏                                                | 6/2200 [00:35<3:39:15,  6.00s/it]



Aproximando altura y azimuth:   0%|▏                                                | 7/2200 [00:41<3:38:35,  5.98s/it]



Aproximando 

Aproximando altura y azimuth:   3%|█▍                                              | 66/2200 [06:23<3:26:39,  5.81s/it]



Aproximando altura y azimuth:   3%|█▍                                              | 67/2200 [06:29<3:26:41,  5.81s/it]



Aproximando altura y azimuth:   3%|█▍                                              | 68/2200 [06:35<3:26:22,  5.81s/it]



Aproximando altura y azimuth:   3%|█▌                                              | 69/2200 [06:41<3:25:32,  5.79s/it]



Aproximando altura y azimuth:   3%|█▌                                              | 70/2200 [06:46<3:25:24,  5.79s/it]



Aproximando altura y azimuth:   3%|█▌                                              | 71/2200 [06:52<3:24:36,  5.77s/it]



Aproximando altura y azimuth:   3%|█▌                                              | 72/2200 [06:58<3:24:17,  5.76s/it]



Aproximando altura y azimuth:   3%|█▌                                              | 73/2200 [07:04<3:24:39,  5.77s/it]



Aproximando altu

Aproximando altura y azimuth:   6%|██▊                                            | 132/2200 [12:45<3:19:41,  5.79s/it]



Aproximando altura y azimuth:   6%|██▊                                            | 133/2200 [12:51<3:19:06,  5.78s/it]



Aproximando altura y azimuth:   6%|██▊                                            | 134/2200 [12:56<3:18:38,  5.77s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 135/2200 [13:02<3:18:54,  5.78s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 136/2200 [13:08<3:18:23,  5.77s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 137/2200 [13:14<3:17:59,  5.76s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 138/2200 [13:19<3:18:13,  5.77s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 139/2200 [13:25<3:18:20,  5.77s/it]



Aproximando altu

Aproximando altura y azimuth:   9%|████▏                                          | 198/2200 [19:05<3:09:53,  5.69s/it]



Aproximando altura y azimuth:   9%|████▎                                          | 199/2200 [19:10<3:09:50,  5.69s/it]



Aproximando altura y azimuth:   9%|████▎                                          | 200/2200 [19:16<3:10:04,  5.70s/it]



Aproximando altura y azimuth:   9%|████▎                                          | 201/2200 [19:22<3:10:22,  5.71s/it]



Aproximando altura y azimuth:   9%|████▎                                          | 202/2200 [19:27<3:10:45,  5.73s/it]



Aproximando altura y azimuth:   9%|████▎                                          | 203/2200 [19:33<3:10:17,  5.72s/it]



Aproximando altura y azimuth:   9%|████▎                                          | 204/2200 [19:39<3:10:48,  5.74s/it]



Aproximando altura y azimuth:   9%|████▍                                          | 205/2200 [19:45<3:09:58,  5.71s/it]



Aproximando altu

Aproximando altura y azimuth:  12%|█████▋                                         | 264/2200 [25:24<3:04:47,  5.73s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 265/2200 [25:30<3:05:34,  5.75s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 266/2200 [25:36<3:07:23,  5.81s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 267/2200 [25:42<3:10:39,  5.92s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 268/2200 [25:48<3:09:36,  5.89s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 269/2200 [25:54<3:10:52,  5.93s/it]



Aproximando altura y azimuth:  12%|█████▊                                         | 270/2200 [26:00<3:12:46,  5.99s/it]



Aproximando altura y azimuth:  12%|█████▊                                         | 271/2200 [26:06<3:13:39,  6.02s/it]



Aproximando altu

...

Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 2045/2200 [3:19:18<15:02,  5.82s/it]



Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 2046/2200 [3:19:24<14:53,  5.80s/it]



Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 2047/2200 [3:19:30<14:47,  5.80s/it]



Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 2048/2200 [3:19:35<14:43,  5.81s/it]



Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 2049/2200 [3:19:41<14:36,  5.80s/it]



Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 2050/2200 [3:19:47<14:32,  5.81s/it]



Aproximando altura y azimuth:  93%|██████████████████████████████████████████▉   | 2051/2200 [3:19:53<14:27,  5.83s/it]



Aproximando altura y azimuth:  93%|██████████████████████████████████████████▉   | 2052/2200 [3:19:59<14:22,  5.82s/it]



Aproximando altu

Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2111/2200 [3:25:43<08:38,  5.83s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2112/2200 [3:25:49<08:33,  5.84s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2113/2200 [3:25:55<08:28,  5.84s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2114/2200 [3:26:01<08:21,  5.83s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2115/2200 [3:26:06<08:15,  5.83s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2116/2200 [3:26:12<08:11,  5.85s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▎ | 2117/2200 [3:26:18<08:04,  5.84s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▎ | 2118/2200 [3:26:24<07:58,  5.84s/it]



Aproximando altu

Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▌| 2177/2200 [3:32:07<02:14,  5.84s/it]



Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▌| 2178/2200 [3:32:13<02:08,  5.85s/it]



Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▌| 2179/2200 [3:32:19<02:02,  5.83s/it]



Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▌| 2180/2200 [3:32:25<01:56,  5.83s/it]



Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▌| 2181/2200 [3:32:31<01:50,  5.83s/it]



Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▌| 2182/2200 [3:32:36<01:44,  5.83s/it]



Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▋| 2183/2200 [3:32:42<01:39,  5.84s/it]



Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▋| 2184/2200 [3:32:48<01:33,  5.84s/it]



Aproximando altu

Aproximando altura y azimuth: 100%|██████████████████████████████████████████████| 2200/2200 [3:34:21<00:00,  5.85s/it]


array([ 4.37875766e-02,  5.19853314e-03,  1.05416567e+00,  7.33610329e-02,
       -5.24112025e-02, -1.39156740e-01,  4.41635759e-03,  4.71369350e-03,
        2.74820813e+00, -1.02665758e-01,  7.30572294e+02,  5.05444291e+02,
       -1.83144878e+00])

In [117]:
result_var_center = np.array([ 4.37875766e-02,  5.19853314e-03,  1.05416567e+00,  7.33610329e-02,
       -5.24112025e-02, -1.39156740e-01,  4.41635759e-03,  4.71369350e-03,
        2.74820813e+00, -1.02665758e-01,  7.30572294e+02,  5.05444291e+02,
       -1.83144878e+00])

In [107]:
mega_alt_xi(results_list[-1])/len(x_exp)

2.1548216119125754

Es curioso que el cenith lo posiciona en (731, 506)

#### Probaremos amoeba con todos los parametros

In [136]:
def amoeba(params, mega_alt_xi, mega_az_xi):
    new_alt_params = optimize.fmin(mega_alt_xi, params, maxfun=1100)
    new_az_params = optimize.fmin(mega_az_xi, params, maxfun=1100)
    return [new_alt_params, new_az_params]

In [139]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
data = drop_outlayers_by_center(data, X0, Y0, 1)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = np.rad2deg(np.arccos(np.cos(np.deg2rad(data.az.values))))
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo)
results_list = []

init_params = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664, 0.0682171007,
                         0.00310608468, -5.75141386e-05, 4.26865327e-06, -0.00415889519,
                           0.005383738310580881, 0.0014950622892165601, float(724), float(472), float(1*np.pi/4)])









Droping Outlayers:   0%|                                                                      | 0/2000 [00:00<?, ?it/s]







Droping Outlayers:   1%|▋                                                           | 23/2000 [00:00<00:08, 223.93it/s]







Droping Outlayers:   2%|█▍                                                          | 48/2000 [00:00<00:08, 228.80it/s]







Droping Outlayers:   4%|██▏                                                         | 72/2000 [00:00<00:08, 230.22it/s]







Droping Outlayers:   5%|██▊                                                         | 95/2000 [00:00<00:08, 228.29it/s]







Droping Outlayers:   6%|███▌                                                       | 119/2000 [00:00<00:08, 229.20it/s]







Droping Outlayers:   7%|████▏                                                      | 143/2000 [00:00<00:08, 229.86it/s]







Droping Outlayers:   8%|████▉                                                      | 166/2000 [00:00<00

Droping Outlayers:  76%|███████████████████████████████████████████▊              | 1511/2000 [00:06<00:02, 229.33it/s]







Droping Outlayers:  77%|████████████████████████████████████████████▍             | 1534/2000 [00:06<00:02, 227.00it/s]







Droping Outlayers:  78%|█████████████████████████████████████████████▏            | 1557/2000 [00:06<00:01, 225.40it/s]







Droping Outlayers:  79%|█████████████████████████████████████████████▊            | 1581/2000 [00:06<00:01, 228.46it/s]







Droping Outlayers:  80%|██████████████████████████████████████████████▌           | 1605/2000 [00:07<00:01, 231.31it/s]







Droping Outlayers:  81%|███████████████████████████████████████████████▏          | 1629/2000 [00:07<00:01, 230.00it/s]







Droping Outlayers:  83%|███████████████████████████████████████████████▉          | 1653/2000 [00:07<00:01, 229.10it/s]







Droping Outlayers:  84%|████████████████████████████████████████████████▌         | 1676/2000 [00:07<00:01, 228

In [140]:
pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
results_list += amoeba(init_params, mega_alt_xi, mega_az_xi)
pbar.close()
for i in range(3):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba(results_list[-1], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]









Aproximando altura y azimuth:   0%|                                                           | 0/2200 [00:00<?, ?it/s]







Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:04<2:47:33,  4.57s/it]







Aproximando altura y azimuth:   0%|                                                 | 2/2200 [00:09<2:47:23,  4.57s/it]







Aproximando altura y azimuth:   0%|                                                 | 3/2200 [00:13<2:47:38,  4.58s/it]







Aproximando altura y azimuth:   0%|                                                 | 4/2200 [00:18<2:47:20,  4.57s/it]







Aproximando altura y azimuth:   0%|                                                 | 5/2200 [00:22<2:47:04,  4.57s/it]







Aproximando altura y azimuth:   0%|▏                                                | 6/2200 [00:27<2:46:56,  4.57s/it]







Aproximando altura y azimuth:   0%|▏                                                | 7/2200 [00:31<2:4

Aproximando altura y azimuth:   3%|█▍                                              | 64/2200 [04:53<2:42:43,  4.57s/it]







Aproximando altura y azimuth:   3%|█▍                                              | 65/2200 [04:57<2:42:59,  4.58s/it]







Aproximando altura y azimuth:   3%|█▍                                              | 66/2200 [05:02<2:42:34,  4.57s/it]







Aproximando altura y azimuth:   3%|█▍                                              | 67/2200 [05:06<2:42:27,  4.57s/it]







Aproximando altura y azimuth:   3%|█▍                                              | 68/2200 [05:11<2:42:21,  4.57s/it]







Aproximando altura y azimuth:   3%|█▌                                              | 69/2200 [05:15<2:42:14,  4.57s/it]







Aproximando altura y azimuth:   3%|█▌                                              | 70/2200 [05:20<2:41:47,  4.56s/it]







Aproximando altura y azimuth:   3%|█▌                                              | 71/2200 [05:25<2:41:29,  4

Aproximando altura y azimuth:   6%|██▋                                            | 128/2200 [09:45<2:36:21,  4.53s/it]







Aproximando altura y azimuth:   6%|██▊                                            | 129/2200 [09:50<2:36:20,  4.53s/it]







Aproximando altura y azimuth:   6%|██▊                                            | 130/2200 [09:54<2:36:03,  4.52s/it]







Aproximando altura y azimuth:   6%|██▊                                            | 131/2200 [09:59<2:35:54,  4.52s/it]







Aproximando altura y azimuth:   6%|██▊                                            | 132/2200 [10:03<2:35:58,  4.53s/it]







Aproximando altura y azimuth:   6%|██▊                                            | 133/2200 [10:08<2:36:07,  4.53s/it]







Aproximando altura y azimuth:   6%|██▊                                            | 134/2200 [10:13<2:36:07,  4.53s/it]







Aproximando altura y azimuth:   6%|██▉                                            | 135/2200 [10:17<2:36:03,  4

Aproximando altura y azimuth:   9%|████                                           | 192/2200 [14:36<2:31:31,  4.53s/it]







Aproximando altura y azimuth:   9%|████                                           | 193/2200 [14:40<2:31:16,  4.52s/it]







Aproximando altura y azimuth:   9%|████▏                                          | 194/2200 [14:45<2:31:19,  4.53s/it]







Aproximando altura y azimuth:   9%|████▏                                          | 195/2200 [14:49<2:31:06,  4.52s/it]







Aproximando altura y azimuth:   9%|████▏                                          | 196/2200 [14:54<2:31:05,  4.52s/it]







Aproximando altura y azimuth:   9%|████▏                                          | 197/2200 [14:59<2:31:32,  4.54s/it]







Aproximando altura y azimuth:   9%|████▏                                          | 198/2200 [15:03<2:31:25,  4.54s/it]







Aproximando altura y azimuth:   9%|████▎                                          | 199/2200 [15:08<2:31:10,  4

Aproximando altura y azimuth:  12%|█████▍                                         | 256/2200 [19:26<2:27:35,  4.56s/it]







Aproximando altura y azimuth:  12%|█████▍                                         | 257/2200 [19:30<2:27:25,  4.55s/it]







Aproximando altura y azimuth:  12%|█████▌                                         | 258/2200 [19:35<2:28:05,  4.58s/it]







Aproximando altura y azimuth:  12%|█████▌                                         | 259/2200 [19:40<2:27:43,  4.57s/it]







Aproximando altura y azimuth:  12%|█████▌                                         | 260/2200 [19:44<2:27:11,  4.55s/it]







Aproximando altura y azimuth:  12%|█████▌                                         | 261/2200 [19:49<2:26:57,  4.55s/it]







Aproximando altura y azimuth:  12%|█████▌                                         | 262/2200 [19:53<2:26:27,  4.53s/it]







Aproximando altura y azimuth:  12%|█████▌                                         | 263/2200 [19:58<2:26:52,  4

...

Aproximando altura y azimuth:  94%|███████████████████████████████████████████   | 2061/2200 [3:15:26<16:03,  6.93s/it]







Aproximando altura y azimuth:  94%|███████████████████████████████████████████   | 2062/2200 [3:15:33<15:56,  6.93s/it]







Aproximando altura y azimuth:  94%|███████████████████████████████████████████▏  | 2063/2200 [3:15:39<15:48,  6.92s/it]







Aproximando altura y azimuth:  94%|███████████████████████████████████████████▏  | 2064/2200 [3:15:46<15:44,  6.94s/it]







Aproximando altura y azimuth:  94%|███████████████████████████████████████████▏  | 2065/2200 [3:15:53<15:35,  6.93s/it]







Aproximando altura y azimuth:  94%|███████████████████████████████████████████▏  | 2066/2200 [3:16:00<15:26,  6.92s/it]







Aproximando altura y azimuth:  94%|███████████████████████████████████████████▏  | 2067/2200 [3:16:07<15:25,  6.96s/it]







Aproximando altura y azimuth:  94%|███████████████████████████████████████████▏  | 2068/2200 [3:16:14<15:16,  6

Aproximando altura y azimuth:  97%|████████████████████████████████████████████▍ | 2125/2200 [3:22:50<08:43,  6.98s/it]







Aproximando altura y azimuth:  97%|████████████████████████████████████████████▍ | 2126/2200 [3:22:57<08:34,  6.95s/it]







Aproximando altura y azimuth:  97%|████████████████████████████████████████████▍ | 2127/2200 [3:23:04<08:28,  6.97s/it]







Aproximando altura y azimuth:  97%|████████████████████████████████████████████▍ | 2128/2200 [3:23:11<08:20,  6.94s/it]







Aproximando altura y azimuth:  97%|████████████████████████████████████████████▌ | 2129/2200 [3:23:18<08:12,  6.94s/it]







Aproximando altura y azimuth:  97%|████████████████████████████████████████████▌ | 2130/2200 [3:23:25<08:05,  6.93s/it]







Aproximando altura y azimuth:  97%|████████████████████████████████████████████▌ | 2131/2200 [3:23:32<07:57,  6.92s/it]







Aproximando altura y azimuth:  97%|████████████████████████████████████████████▌ | 2132/2200 [3:23:39<07:49,  6

Aproximando altura y azimuth: 100%|█████████████████████████████████████████████▊| 2189/2200 [3:30:16<01:16,  6.97s/it]







Aproximando altura y azimuth: 100%|█████████████████████████████████████████████▊| 2190/2200 [3:30:23<01:09,  6.96s/it]







Aproximando altura y azimuth: 100%|█████████████████████████████████████████████▊| 2191/2200 [3:30:30<01:02,  6.97s/it]







Aproximando altura y azimuth: 100%|█████████████████████████████████████████████▊| 2192/2200 [3:30:37<00:55,  6.99s/it]







Aproximando altura y azimuth: 100%|█████████████████████████████████████████████▊| 2193/2200 [3:30:44<00:48,  7.00s/it]







Aproximando altura y azimuth: 100%|█████████████████████████████████████████████▊| 2194/2200 [3:30:51<00:41,  6.99s/it]







Aproximando altura y azimuth: 100%|█████████████████████████████████████████████▉| 2195/2200 [3:30:58<00:34,  6.96s/it]







Aproximando altura y azimuth: 100%|█████████████████████████████████████████████▉| 2196/2200 [3:31:05<00:27,  6

Aproximando altura y azimuth: 100%|██████████████████████████████████████████████| 2200/2200 [3:31:32<00:00,  5.77s/it]


array([ 3.72624114e-02,  1.33736985e+00,  2.38002088e-01,  7.75240777e-04,
        3.45199068e-03, -2.97311198e-03,  2.67780817e-04,  4.53655569e-03,
        1.41563190e+00,  5.65744491e-03,  7.56539056e+02,  4.37558301e+02,
        2.26330325e+00])

In [141]:
result_brute = np.array([ 3.72624114e-02,  1.33736985e+00,  2.38002088e-01,  7.75240777e-04,
        3.45199068e-03, -2.97311198e-03,  2.67780817e-04,  4.53655569e-03,
        1.41563190e+00,  5.65744491e-03,  7.56539056e+02,  4.37558301e+02,
        2.26330325e+00])

In [173]:
mega_alt_xi(result_brute)/len(x_exp)

2179.1656267468356

Muy mal resultado... 

#### Otra forma
- primero reduciremos los datos para eliminar los outlayers excesivos
- luego definiremos $(x_0,y_0)=724, 483$ y $a_0=\frac{\pi}{4}$
- luego reduciremos datos discriminando por una diferencia grande de altura con respecto a las funciones de borovicka
- los paramtros iniciales serán los del resultado 314 y reduciremos altura segun el metodo 314
- luego probraremos reducir solo azimuth usando dejando solo a0, E y ep
- (podemos tambien intentar repetir esto mismo pero con altura y azimuth en todo momento)

In [148]:
plot_azimuth(result_brute)

In [202]:
def construct_radio(C, A, F, X0, Y0, a0):
    def r(x, y):
        return C * ( np.sqrt( (x-X0)**2 + (y-Y0)**2 ) + A*(y-X0)*np.cos(F-a0) - A*(x-X0)*np.sin(F-a0) )
    return r

def construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0):
    def u(x, y):
        r = construct_radio(C, A, F, X0, Y0, a0)
        return V*r(x, y) + S*(np.e**(D*r(x,y)) - 1) + P*(np.e**(Q*r(x,y)**2) - 1) 
    return u

def construct_b(E, X0, Y0, a0):
    def b(x, y):
        return a0 - E + np.arctan2((y - Y0),(x - X0))
    return b

def construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        return np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) )
    return z

def construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        return 90 - np.rad2deg( np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) ) )
    return z

def construct_azimuth(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E
    return az

def construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return np.rad2deg( np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E ) + 90
    return az

def construct_alt_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
        alt_teorico = construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return (z - alt_teorico(x, y))**2
    return xi

def construct_az_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
        az_teorico = construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return (z - az_teorico(x, y))**2
    return xi

######################################################################################################
"""
METODO 314
"""


def construct_acumulate_alt_xi(x_list, y_list, z_list, ctes = None):
    def acumulate_xi(params):
        V, S, D, P, Q, X0, Y0, a0 = ctes
        C, A, F, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        pbar.update()
        return suma_xi
    return acumulate_xi

def construct_acumulate_az_xi(x_list, y_list, z_list, ctes = None):
    def acumulate_xi(params):
        V, S, D, P, Q, X0, Y0, a0 = ctes
        C, A, F, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_az_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        pbar.update()
        return suma_xi
    return acumulate_xi

######################################################################################################

def amoeba(params, mega_alt_xi, mega_az_xi):
    new_alt_params = optimize.fmin(mega_alt_xi, params, maxfun=1100)
#     new_az_params = optimize.fmin(mega_az_xi, params, maxfun=1100)
    return [new_alt_params]

In [194]:
X0, Y0, a0 = float(724), float(483), float(1*np.pi/4)
V, S, D, P, Q = result_314[3:8]
C, A, F, E, ep = *result_314[:3], *result_314[-2:]

ctes = [V, S, D, P, Q, X0, Y0, a0]

data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
data = drop_outlayers_by_borovicka(data, construct_altura_deg(*result_314, X0, Y0, a0), 5)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = np.rad2deg(np.arccos(np.cos(np.deg2rad(data.az.values))))
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo, ctes)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo, ctes)
results_list = []

init_params = np.array([C, A, F, E, ep])















Droping Outlayers:   0%|                                                                     | 0/80771 [00:00<?, ?it/s]













Droping Outlayers:   1%|▍                                                        | 686/80771 [00:00<00:11, 6808.36it/s]













Droping Outlayers:   2%|▉                                                       | 1367/80771 [00:00<00:11, 6793.98it/s]













Droping Outlayers:   3%|█▍                                                      | 2053/80771 [00:00<00:11, 6798.85it/s]













Droping Outlayers:   3%|█▉                                                      | 2752/80771 [00:00<00:11, 6840.38it/s]













Droping Outlayers:   4%|██▍                                                     | 3442/80771 [00:00<00:11, 6843.83it/s]













Droping Outlayers:   5%|██▊                                                     | 4108/80771 [00:00<00:11, 6772.49it/s]













Droping Outlayers:   6%|███▎                           

Droping Outlayers:  52%|████████████████████████████▌                          | 41927/80771 [00:06<00:05, 6921.86it/s]













Droping Outlayers:  53%|█████████████████████████████                          | 42626/80771 [00:06<00:05, 6927.07it/s]













Droping Outlayers:  54%|█████████████████████████████▌                         | 43334/80771 [00:06<00:05, 6957.33it/s]













Droping Outlayers:  55%|█████████████████████████████▉                         | 44030/80771 [00:06<00:05, 6761.24it/s]













Droping Outlayers:  55%|██████████████████████████████▍                        | 44708/80771 [00:06<00:05, 6164.29it/s]













Droping Outlayers:  56%|██████████████████████████████▉                        | 45406/80771 [00:06<00:05, 6375.51it/s]













Droping Outlayers:  57%|███████████████████████████████▍                       | 46101/80771 [00:06<00:05, 6523.54it/s]













Droping Outlayers:  58%|███████████████████████████████▊             

In [200]:
mega_alt_xi(init_params)/len(x_exp)

















Aproximando altura y azimuth:   1%|▎                                                | 8/1100 [01:43<5:47:23, 19.09s/it]

3.5823653463976477

In [201]:
pbar = tqdm(total=1100, desc="Aproximando altura y azimuth")
results_list += amoeba(init_params, mega_alt_xi, mega_az_xi)
pbar.close()
results_list[-1]


















Aproximando altura y azimuth:   0%|                                                           | 0/1100 [00:00<?, ?it/s]
















Aproximando altura y azimuth:   0%|                                                 | 1/1100 [00:04<1:28:59,  4.86s/it]
















Aproximando altura y azimuth:   0%|                                                 | 2/1100 [00:09<1:28:58,  4.86s/it]
















Aproximando altura y azimuth:   0%|▏                                                | 3/1100 [00:14<1:28:56,  4.86s/it]
















Aproximando altura y azimuth:   0%|▏                                                | 4/1100 [00:19<1:28:32,  4.85s/it]
















Aproximando altura y azimuth:   0%|▏                                                | 5/1100 [00:24<1:28:51,  4.87s/it]
















Aproximando altura y azimuth:   1%|▎                                                | 6/1100 [00:29<1:30:08,  4.94s/it]
















Aproximando altura y azimuth:  

Aproximando altura y azimuth:   5%|██▌                                             | 60/1100 [04:57<1:24:04,  4.85s/it]
















Aproximando altura y azimuth:   6%|██▋                                             | 61/1100 [05:02<1:24:18,  4.87s/it]
















Aproximando altura y azimuth:   6%|██▋                                             | 62/1100 [05:07<1:25:42,  4.95s/it]
















Aproximando altura y azimuth:   6%|██▋                                             | 63/1100 [05:12<1:25:14,  4.93s/it]
















Aproximando altura y azimuth:   6%|██▊                                             | 64/1100 [05:17<1:24:56,  4.92s/it]
















Aproximando altura y azimuth:   6%|██▊                                             | 65/1100 [05:22<1:25:00,  4.93s/it]
















Aproximando altura y azimuth:   6%|██▉                                             | 66/1100 [05:27<1:25:41,  4.97s/it]
















Aproximando altura y azimuth:   6%|██▉          

Aproximando altura y azimuth:  11%|█████▏                                         | 120/1100 [09:54<1:21:22,  4.98s/it]
















Aproximando altura y azimuth:  11%|█████▏                                         | 121/1100 [09:59<1:21:12,  4.98s/it]
















Aproximando altura y azimuth:  11%|█████▏                                         | 122/1100 [10:04<1:20:50,  4.96s/it]
















Aproximando altura y azimuth:  11%|█████▎                                         | 123/1100 [10:09<1:21:01,  4.98s/it]
















Aproximando altura y azimuth:  11%|█████▎                                         | 124/1100 [10:14<1:20:26,  4.95s/it]
















Aproximando altura y azimuth:  11%|█████▎                                         | 125/1100 [10:19<1:19:57,  4.92s/it]
















Aproximando altura y azimuth:  11%|█████▍                                         | 126/1100 [10:24<1:20:32,  4.96s/it]
















Aproximando altura y azimuth:  12%|█████▍       

Aproximando altura y azimuth:  16%|███████▋                                       | 180/1100 [14:53<1:14:02,  4.83s/it]
















Aproximando altura y azimuth:  16%|███████▋                                       | 181/1100 [14:58<1:13:49,  4.82s/it]
















Aproximando altura y azimuth:  17%|███████▊                                       | 182/1100 [15:03<1:14:43,  4.88s/it]
















Aproximando altura y azimuth:  17%|███████▊                                       | 183/1100 [15:08<1:15:14,  4.92s/it]
















Aproximando altura y azimuth:  17%|███████▊                                       | 184/1100 [15:13<1:15:06,  4.92s/it]
















Aproximando altura y azimuth:  17%|███████▉                                       | 185/1100 [15:18<1:14:50,  4.91s/it]
















Aproximando altura y azimuth:  17%|███████▉                                       | 186/1100 [15:23<1:14:21,  4.88s/it]
















Aproximando altura y azimuth:  17%|███████▉     

Aproximando altura y azimuth:  22%|██████████▎                                    | 240/1100 [19:46<1:10:10,  4.90s/it]
















Aproximando altura y azimuth:  22%|██████████▎                                    | 241/1100 [19:51<1:09:46,  4.87s/it]
















Aproximando altura y azimuth:  22%|██████████▎                                    | 242/1100 [19:56<1:10:02,  4.90s/it]
















Aproximando altura y azimuth:  22%|██████████▍                                    | 243/1100 [20:01<1:09:52,  4.89s/it]
















Aproximando altura y azimuth:  22%|██████████▍                                    | 244/1100 [20:05<1:09:24,  4.87s/it]
















Aproximando altura y azimuth:  22%|██████████▍                                    | 245/1100 [20:10<1:09:46,  4.90s/it]
















Aproximando altura y azimuth:  22%|██████████▌                                    | 246/1100 [20:15<1:09:26,  4.88s/it]
















Aproximando altura y azimuth:  22%|██████████▌  

...

Aproximando altura y azimuth:  82%|██████████████████████████████████████▍        | 900/1100 [1:13:58<16:26,  4.93s/it]
















Aproximando altura y azimuth:  82%|██████████████████████████████████████▍        | 901/1100 [1:14:02<16:16,  4.91s/it]
















Aproximando altura y azimuth:  82%|██████████████████████████████████████▌        | 902/1100 [1:14:07<16:10,  4.90s/it]
















Aproximando altura y azimuth:  82%|██████████████████████████████████████▌        | 903/1100 [1:14:12<16:04,  4.89s/it]
















Aproximando altura y azimuth:  82%|██████████████████████████████████████▋        | 904/1100 [1:14:17<15:57,  4.88s/it]
















Aproximando altura y azimuth:  82%|██████████████████████████████████████▋        | 905/1100 [1:14:22<15:54,  4.90s/it]
















Aproximando altura y azimuth:  82%|██████████████████████████████████████▋        | 906/1100 [1:14:27<16:03,  4.97s/it]
















Aproximando altura y azimuth:  82%|█████████████

Aproximando altura y azimuth:  87%|█████████████████████████████████████████      | 960/1100 [1:18:53<11:22,  4.87s/it]
















Aproximando altura y azimuth:  87%|█████████████████████████████████████████      | 961/1100 [1:18:58<11:16,  4.87s/it]
















Aproximando altura y azimuth:  87%|█████████████████████████████████████████      | 962/1100 [1:19:03<11:13,  4.88s/it]
















Aproximando altura y azimuth:  88%|█████████████████████████████████████████▏     | 963/1100 [1:19:08<11:08,  4.88s/it]
















Aproximando altura y azimuth:  88%|█████████████████████████████████████████▏     | 964/1100 [1:19:13<11:04,  4.88s/it]
















Aproximando altura y azimuth:  88%|█████████████████████████████████████████▏     | 965/1100 [1:19:18<11:02,  4.90s/it]
















Aproximando altura y azimuth:  88%|█████████████████████████████████████████▎     | 966/1100 [1:19:22<10:55,  4.89s/it]
















Aproximando altura y azimuth:  88%|█████████████

Aproximando altura y azimuth:  93%|██████████████████████████████████████████▋   | 1020/1100 [1:23:46<06:28,  4.85s/it]
















Aproximando altura y azimuth:  93%|██████████████████████████████████████████▋   | 1021/1100 [1:23:51<06:24,  4.87s/it]
















Aproximando altura y azimuth:  93%|██████████████████████████████████████████▋   | 1022/1100 [1:23:55<06:18,  4.86s/it]
















Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 1023/1100 [1:24:00<06:13,  4.86s/it]
















Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 1024/1100 [1:24:05<06:08,  4.85s/it]
















Aproximando altura y azimuth:  93%|██████████████████████████████████████████▊   | 1025/1100 [1:24:10<06:02,  4.84s/it]
















Aproximando altura y azimuth:  93%|██████████████████████████████████████████▉   | 1026/1100 [1:24:15<05:57,  4.83s/it]
















Aproximando altura y azimuth:  93%|█████████████

Aproximando altura y azimuth:  98%|█████████████████████████████████████████████▏| 1080/1100 [1:28:40<01:37,  4.86s/it]
















Aproximando altura y azimuth:  98%|█████████████████████████████████████████████▏| 1081/1100 [1:28:45<01:32,  4.84s/it]
















Aproximando altura y azimuth:  98%|█████████████████████████████████████████████▏| 1082/1100 [1:28:50<01:27,  4.86s/it]
















Aproximando altura y azimuth:  98%|█████████████████████████████████████████████▎| 1083/1100 [1:28:55<01:22,  4.87s/it]
















Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▎| 1084/1100 [1:29:00<01:17,  4.87s/it]
















Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▎| 1085/1100 [1:29:04<01:12,  4.86s/it]
















Aproximando altura y azimuth:  99%|█████████████████████████████████████████████▍| 1086/1100 [1:29:09<01:07,  4.86s/it]
















Aproximando altura y azimuth:  99%|█████████████

NameError: name 'new_az_params' is not defined

In [185]:
plt.gca().invert_yaxis()
plt.scatter(x_exp, y_exp, c=alt_catalogo, s=0.01)
len(x_exp)

80043

In [186]:
#out = drop_outlayers_by_borovicka(data, X0, Y0)
out = data
out["xcentroid"] = out["x"]
out["ycentroid"] = out["y"]
out.to_csv("drop_outlayer.dat", sep=' ', index=False)
plt.gca().invert_yaxis()
plt.scatter(out.x.values, out.y.values, c=out.alt.values, s=0.01)











Droping Outlayers: 100%|███████████████████████████████████████████████████████| 80771/80771 [00:27<00:00, 6564.61it/s]

In [190]:
result_314[-2:]

array([0.00538374, 0.00149506])